In [1]:

import numpy as np
import pandas as pd
from sklearn import preprocessing
import matplotlib.pyplot as plt
import plotly.express as px
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import mutual_info_regression
import plotly.graph_objects as go
from tqdm import tqdm  # Import tqdm for the progress bar
from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer


In [2]:

sales_data = pd.read_csv('Dataset/saleshourly.csv')
sales_data.head()


datum  M01AB  M01AE  N02BA  N02BE  N05B  N05C  R03  R06  Year   
0   1/2/2014 8:00    0.0   0.67    0.4    2.0   0.0   0.0  0.0  1.0  2014  \
1   1/2/2014 9:00    0.0   0.00    1.0    0.0   2.0   0.0  0.0  0.0  2014   
2  1/2/2014 10:00    0.0   0.00    0.0    3.0   2.0   0.0  0.0  0.0  2014   
3  1/2/2014 11:00    0.0   0.00    0.0    2.0   1.0   0.0  0.0  0.0  2014   
4  1/2/2014 12:00    0.0   2.00    0.0    5.0   2.0   0.0  0.0  0.0  2014   

   Month  Hour Weekday Name  
0      1     8     Thursday  
1      1     9     Thursday  
2      1    10     Thursday  
3      1    11     Thursday  
4      1    12     Thursday

In [3]:

import pandas as pd
from pandas.tseries.holiday import USFederalHolidayCalendar

def date_time_features(df, date_col):
    df = df.copy()
    df['date'] = pd.to_datetime(df[date_col])
    df = df.drop(columns=([date_col] + ['Month', 'Year', 'Hour']))
    
    # Basic features
    df['month'] = df['date'].dt.month
    df['quarter'] = df['date'].dt.quarter
    
    # Additional features
    df['weekday'] = df['date'].dt.weekday  # Monday=0, Sunday=6
    df['is_weekend'] = df['weekday'] >= 5  # Saturday and Sunday
    df['is_month_start'] = df['date'].dt.is_month_start
    df['is_month_end'] = df['date'].dt.is_month_end   
    df['is_working_hours'] = df['date'].dt.hour.between(9, 19)  # Assuming typical working hours
    df['is_day'] = ~df['date'].dt.hour.between(0, 6) | df['date'].dt.hour.between(20, 23)

    
    # Hourly data specific features
    df['hour'] = df['date'].dt.hour
    
    # Time of day segments
    def get_time_of_day(hour):
        if 5 <= hour < 12:
            return 'Morning'
        elif 12 <= hour < 17:
            return 'Afternoon'
        elif 17 <= hour < 21:
            return 'Evening'
        else:
            return 'Night'
    
    df['time_of_day'] = df['hour'].apply(get_time_of_day)
    
    # Season (assuming Northern Hemisphere)
    df['season'] = df['date'].dt.month % 12 // 3 + 1
    df['season'] = df['season'].replace({1: 'Winter', 2: 'Spring', 3: 'Summer', 4: 'Fall'})
    
    # US Federal Holidays
    cal = USFederalHolidayCalendar()
    holidays = cal.holidays(start=df['date'].min(), end=df['date'].max())
    df['is_holiday'] = df['date'].dt.floor('d').isin(holidays)
    
    return df


In [4]:

sales_data_with_features = date_time_features(sales_data, 'datum')
# sales_data_with_features.info()


In [7]:
sales_data_with_features

Index(['M01AB', 'M01AE', 'N02BA', 'N02BE', 'N05B', 'N05C', 'R03', 'R06',
       'Weekday Name', 'date', 'month', 'quarter', 'weekday', 'is_weekend',
       'is_month_start', 'is_month_end', 'is_working_hours', 'is_day', 'hour',
       'time_of_day', 'season', 'is_holiday'],
      dtype='object')

In [9]:

# Function to calculate ADI
def calculate_ADI(data, cols):
    ADIs = {}
    for col in cols:
        non_zero_demand = data[col].astype(bool).sum()
        ADI = data.shape[0] / non_zero_demand if non_zero_demand else 0
        ADIs[col] = ADI
    adi_df = pd.DataFrame.from_dict(ADIs, orient='index', columns=['ADI'])
    return adi_df

# Specify the columns of interest
cols = ['M01AB', 'M01AE', 'N02BA', 'N02BE', 'N05B', 'N05C', 'R03', 'R06']

# Apply the function to calculate ADI
adi_scores = calculate_ADI(sales_data_with_features, cols)
adi_scores


ADI
M01AB   5.678391
M01AE   5.310772
N02BA   6.786463
N02BE   2.476816
N05B    4.786134
N05C   58.486111
R03    14.810082
R06     9.561400

In [24]:
import pandas as pd
import plotly.graph_objects as go

def plot_time_series(sales_data_with_features, cols, scale_features=False, include_features=True, start_date='01-01-2014'):
    """
    Plot time series for selected features and Sales using Plotly.

    Parameters:
    sales_data_with_features (pd.DataFrame): DataFrame containing all features, Sales, date, and correlation data.
    cols (list): The list of columns to be plotted.
    scale_features (bool): Whether to scale the features by mean normalization.
    include_features (bool): Whether to include the additional features in the plot.
    start_date (str): The start date from which to plot the time series.
    """
    # Ensure 'date' is in datetime format
    sales_data_with_features['date'] = pd.to_datetime(sales_data_with_features['date'])
    sales_data_with_features = sales_data_with_features[sales_data_with_features['date'] > pd.to_datetime(start_date)]

    # Copy the original DataFrame
    df_filtered = sales_data_with_features.copy()

    if scale_features:
        # Mean normalization for all numerical columns
        numerical_cols = df_filtered.select_dtypes(include=['int', 'float']).columns
        df_filtered[numerical_cols] = (df_filtered[numerical_cols] - df_filtered[numerical_cols].mean()) / df_filtered[numerical_cols].std()
        
    # Initialize the figure
    fig = go.Figure()
    
    for col in cols:
        # Add trace for the current product column
        fig.add_trace(go.Scatter(x=df_filtered['date'], y=df_filtered[col],
                                 mode='lines', name=col))
        
    if include_features:
        # Add traces for each date-time feature
        for feature in df_filtered.columns:
            if feature not in ['date'] + cols:
                fig.add_trace(go.Scatter(x=df_filtered['date'], y=df_filtered[feature],
                                         mode='lines', name=feature, line=dict(dash='dash')))
    
    # Update layout
    fig.update_layout(title=f"Time Series Plot for {', '.join(cols)}",
                      xaxis_title="Date",
                      yaxis_title="Value",
                      legend_title="Features",
                      template="plotly_white")
    
    # Show the plot
    fig.show()

# Sales columns for different products 
cols = ['M01AB', 'M01AE', 'N02BA', 'N02BE', 'N05B', 'N05C', 'R03', 'R06']

# Plot the time series without features
plot_time_series(sales_data_with_features, ['M01AB'], scale_features=True, include_features=False)


In [25]:
data_types = sales_data_with_features.dtypes

# Identify categorical and numerical columns
categorical_features = data_types[(data_types == 'object') | (data_types == 'bool')].index.tolist()
numerical_features = data_types[(data_types == 'int32') | (data_types == 'int64') | (data_types == 'float64')].index.tolist()

numerical_features = list(set(numerical_features) - set(cols))
sales_columns = cols

# Print the list of categorical columns
print("Sales Columns:", sales_columns)
print("Numerical Features:", numerical_features)
print("Categorical Features:", categorical_features)



Sales Columns: ['M01AB', 'M01AE', 'N02BA', 'N02BE', 'N05B', 'N05C', 'R03', 'R06']
Numerical Features: ['quarter', 'weekday', 'month', 'hour']
Categorical Features: ['Weekday Name', 'is_weekend', 'is_month_start', 'is_month_end', 'is_working_hours', 'is_day', 'time_of_day', 'season', 'is_holiday']


In [26]:

select_features = True
def select_features_randomforest(X, y, k=5):
    model = RandomForestRegressor(n_estimators=100, random_state=42)
    model.fit(X, y)
    feature_importances = pd.Series(model.feature_importances_, index=X.columns)
    top_features = feature_importances.nlargest(k).index
    return top_features



from sklearn.feature_selection import mutual_info_regression

def select_features_regression(X, y, k=5):
    # Select top k features based on mutual information
    selector = SelectKBest(mutual_info_regression, k=k)
    X_selected = selector.fit_transform(X, y)
    selected_features = X.columns[selector.get_support()]
    return selected_features


In [27]:
# Iterate through each product column
for col in tqdm(sales_columns, desc="Processing Columns"):
    subset_df = sales_data_with_features[['date', col] + categorical_features + numerical_features].copy()
    y = subset_df[col]
    X = subset_df.drop(columns=[col, 'date'])
    
    preprocessor = ColumnTransformer(
        transformers=[
            ('cat', OneHotEncoder(handle_unknown='ignore'), categorical_features)
        ],
        remainder='passthrough'
    )
    
    X_encoded = preprocessor.fit_transform(X)
    feature_names = preprocessor.get_feature_names_out()
    clean_feature_names = [name.replace('cat__', '').replace('remainder__', '') for name in feature_names]
    X_encoded_df = pd.DataFrame(X_encoded, columns=clean_feature_names)
    if select_features:
         top_features = select_features_regression(X_encoded_df, y, k=5)
         X_encoded_df = X_encoded_df[top_features]
    
    Encoded_df = X_encoded_df.merge(subset_df[['date', col]].reset_index(drop=True), right_index=True, left_index=True)
    
    plot_time_series(Encoded_df,[col],scale_features=True,include_features=True,start_date='01-01-2019')
    break

Processing Columns:   0%|          | 0/8 [00:00<?, ?it/s]

Processing Columns:   0%|          | 0/8 [00:10<?, ?it/s]


In [28]:

def identify_dst_transitions(start_year, end_year):
    """
    Identify potential DST transition dates for the given year range.
    Returns a list of tuples with potential DST start and end dates.
    """
    dst_transitions = []
    for year in range(start_year, end_year + 1):
        # Assuming DST starts on the second Sunday in March and ends on the first Sunday in November
        dst_start = pd.date_range(start=f'{year}-03-01', end=f'{year}-03-14', freq='W-SUN')[1]
        dst_end = pd.date_range(start=f'{year}-11-01', end=f'{year}-11-07', freq='W-SUN')[0]
        dst_transitions.append((dst_start, dst_end))
    return dst_transitions

def check_missing_hours(data, transition_date):
    """
    Check for missing hours on the given transition date.
    """
    transition_day = data[data['date'].dt.date == transition_date.date()].copy()
    expected_hours = set(range(24))
    actual_hours = set(transition_day['date'].dt.hour)
    missing_hours = expected_hours - actual_hours
    return missing_hours

def check_duplicate_hours(data, transition_date):
    """
    Check for duplicate hours on the given transition date.
    """
    transition_day = data[data['date'].dt.date == transition_date.date()].copy()
    duplicate_hours = transition_day['date'].dt.hour.value_counts()
    duplicates = duplicate_hours[duplicate_hours > 1].index.tolist()
    return duplicates

def plot_sales_around_transition(data, transition_date, days=3):
    """
    Plot sales data around the given transition date.
    """
    start_date = transition_date - pd.Timedelta(days=days)
    end_date = transition_date + pd.Timedelta(days=days)
    period_data = data[(data['date'] >= start_date) & (data['date'] <= end_date)].copy()
    
    plt.figure(figsize=(14, 7))
    for col in period_data.columns:
        if col not in ['date', 'weekday', 'Weekday Name', 'time_of_day', 'season', 'is_holiday']:
            plt.plot(period_data['date'], period_data[col], label=col)
    
    plt.axvline(transition_date, color='red', linestyle='--', label='DST Transition')
    plt.xlabel('Date')
    plt.ylabel('Sales')
    plt.title('Sales Data Around DST Transition')
    plt.legend()
    plt.show()



def analyze_dst_effects(data):
    data['date'] = pd.to_datetime(data['date'])
    start_year = data['date'].dt.year.min().copy()
    end_year = data['date'].dt.year.max().copy()
    
    dst_transitions = identify_dst_transitions(start_year, end_year)
    dst_effects_present = False

    for start, end in dst_transitions:
        missing_hours_start = check_missing_hours(data, start)
        duplicate_hours_end = check_duplicate_hours(data, end)
        
        # print(f'DST Start {start}: Missing hours: {missing_hours_start}')
        # print(f'DST End {end}: Duplicate hours: {duplicate_hours_end}')
        
        # plot_sales_around_transition(data, start)
        # plot_sales_around_transition(data, end)
        
        if missing_hours_start or duplicate_hours_end:
            dst_effects_present = True
    
    if dst_effects_present:
        print("Daylight Saving Time effects are present in the data.")
    else:
        print("No Daylight Saving Time effects detected in the data.")



for col in sales_columns:
    sales_data = sales_data_with_features[['date', col]].copy()
    analyze_dst_effects(sales_data)


No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.
No Daylight Saving Time effects detected in the data.


In [29]:
sales_data_with_features

M01AB  M01AE  N02BA  N02BE  N05B  N05C  R03  R06 Weekday Name  \
0       0.00   0.67    0.4    2.0   0.0   0.0  0.0  1.0     Thursday   
1       0.00   0.00    1.0    0.0   2.0   0.0  0.0  0.0     Thursday   
2       0.00   0.00    0.0    3.0   2.0   0.0  0.0  0.0     Thursday   
3       0.00   0.00    0.0    2.0   1.0   0.0  0.0  0.0     Thursday   
4       0.00   2.00    0.0    5.0   2.0   0.0  0.0  0.0     Thursday   
...      ...    ...    ...    ...   ...   ...  ...  ...          ...   
50527   0.00   0.40    0.0   11.3   1.0   0.0  0.0  0.0      Tuesday   
50528   0.33   0.00    0.0    1.0   2.0   0.0  0.0  0.0      Tuesday   
50529   0.00   0.00    0.0    1.0   2.0   0.0  1.0  0.0      Tuesday   
50530   0.00   0.00    0.0    9.0   0.0   0.0  0.0  0.0      Tuesday   
50531   0.00   0.33    0.0    8.0   1.0   0.0  1.0  0.0      Tuesday   

                     date  ...  weekday  is_weekend  is_month_start  \
0     2014-01-02 08:00:00  ...        3       False           False   
1     2014-01-02 09:00:00  ...        3       False           False   
2     2014-01-02 10:00:00  ...        3       False           False   
3     2014-01-02 11:00:00  ...        3       False           False   
4     2014-01-02 12:00:00  ...        3       False           False   
...                   ...  ...      ...         ...             ...   
50527 2019-10-08 15:00:00  ...        1       False           False   
50528 2019-10-08 16:00:00  ...        1       False           False   
50529 2019-10-08 17:00:00  ...        1       False           False   
50530 2019-10-08 18:00:00  ...        1       False           False   
50531 2019-10-08 19:00:00  ...        1       False           False   

       is_month_end  is_working_hours  is_day  hour  time_of_day  season  \
0             False             False    True     8      Morning  Winter   
1             False              True    True     9      Morning  Winter   
2             False              True    True    10      Morning  Winter   
3             False              True    True    11      Morning  Winter   
4             False              True    True    12    Afternoon  Winter   
...             ...               ...     ...   ...          ...     ...   
50527         False              True    True    15    Afternoon    Fall   
50528         False              True    True    16    Afternoon    Fall   
50529         False              True    True    17      Evening    Fall   
50530         False              True    True    18      Evening    Fall   
50531         False              True    True    19      Evening    Fall   

      is_holiday  
0          False  
1          False  
2          False  
3          False  
4          False  
...          ...  
50527      False  
50528      False  
50529      False  
50530      False  
50531      False  

[50532 rows x 22 columns]

In [10]:
import numpy as np
import pandas as pd

def fourier_series_features_hourly(df, date_col, columns, daily_order=5, weekly_order=3, annual_order=3):
    """
    Add Fourier series components to the dataframe for given columns considering daily, weekly, and annual cycles.
    
    Parameters:
    df (pd.DataFrame): The dataframe containing the data.
    date_col (str): The name of the column containing the date information.
    columns (list): The list of columns to which Fourier components will be added.
    daily_order (int): The order of the daily Fourier series.
    weekly_order (int): The order of the weekly Fourier series.
    annual_order (int): The order of the annual Fourier series.
    
    Returns:
    pd.DataFrame: The dataframe with added Fourier series components.
    """
    df = df.copy()
    time = (pd.to_datetime(df[date_col]) - pd.Timestamp('1970-01-01')).dt.total_seconds() / 3600  # Convert to hours
    
    # Daily period (24 hours)
    daily_period = 24
    for i in range(1, daily_order + 1):
        for col in columns:
            df[f'{col}_daily_sin_{i}'] = np.sin(2 * np.pi * i * time / daily_period)
            df[f'{col}_daily_cos_{i}'] = np.cos(2 * np.pi * i * time / daily_period)
    
    # Weekly period (168 hours)
    weekly_period = 168
    for i in range(1, weekly_order + 1):
        for col in columns:
            df[f'{col}_weekly_sin_{i}'] = np.sin(2 * np.pi * i * time / weekly_period)
            df[f'{col}_weekly_cos_{i}'] = np.cos(2 * np.pi * i * time / weekly_period)
    
    # Annual period (8766 hours)
    annual_period = 8766
    for i in range(1, annual_order + 1):
        for col in columns:
            df[f'{col}_annual_sin_{i}'] = np.sin(2 * np.pi * i * time / annual_period)
            df[f'{col}_annual_cos_{i}'] = np.cos(2 * np.pi * i * time / annual_period)
    
    return df

# Example usage
sales_data_with_fourier_hourly = fourier_series_features_hourly(sales_data_with_features, 'date', cols, daily_order=5, weekly_order=3, annual_order=3)


C:\Users\91976\AppData\Local\Temp\ipykernel_20436\1199832064.py:34: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_weekly_cos_{i}'] = np.cos(2 * np.pi * i * time / weekly_period)
C:\Users\91976\AppData\Local\Temp\ipykernel_20436\1199832064.py:33: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{col}_weekly_sin_{i}'] = np.sin(2 * np.pi * i * time / weekly_period)
C:\Users\91976\AppData\Local\Temp\ipykernel_20436\1199832064.py:34: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calli

In [13]:
sales_data_with_fourier_hourly.to_csv('dataset_pharma.csv')

In [31]:
def remove_non_working_hours(df, working_hours_col='is_working_hours'):
    """
    Remove rows where working hours is False.
    
    Parameters:
    df (pd.DataFrame): The dataframe containing the data.
    working_hours_col (str): The name of the column indicating working hours.
    
    Returns:
    pd.DataFrame: The dataframe with non-working hours rows removed.
    """
    return df[df[working_hours_col]]

# Example usage
sales_data_working_hours = remove_non_working_hours(sales_data_with_features, 'is_working_hours')


In [53]:
import pandas as pd
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder

def create_dummy_encoding(df, column_to_encode):
    # Ensure column_to_encode is a list
    if isinstance(column_to_encode, str):
        column_to_encode = [column_to_encode]
    
    preprocessor = ColumnTransformer(
        transformers=[
            ('cat', OneHotEncoder(handle_unknown='ignore'), column_to_encode)
        ],
        remainder='passthrough'  # Keep the remaining columns
    )
    
    # Apply the transformer to the entire dataframe
    X_encoded = preprocessor.fit_transform(df)
    
    # Extract feature names
    feature_names = preprocessor.named_transformers_['cat'].get_feature_names_out(column_to_encode)
    remaining_feature_names = [col for col in df.columns if col not in column_to_encode]
    all_feature_names = list(feature_names) + remaining_feature_names
    
    # Create the encoded dataframe
    X_encoded_df = pd.DataFrame(X_encoded, columns=all_feature_names)
    
    return X_encoded_df

encoded_df = create_dummy_encoding(sales_data_with_features, column_to_encode='hour')
print(encoded_df)


encoded_df = create_dummy_encoding(sales_data_with_features, column_to_encode='weekday')
print(encoded_df)

      hour_0 hour_1 hour_2 hour_3 hour_4 hour_5 hour_6 hour_7 hour_8 hour_9  \
0        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0   
1        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0   
2        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
50527    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
50528    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
50529    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
50530    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
50531    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

       ... quarter weekday is_weekend is_month_star